In [ ]:
import cudf
import numpy as np
import pandas as pd
import plotly.express as px
import semlib
import tools

# init paths to data and models
DATA_PATH = '/data/'

SEM_MODEL_NAME = 'sm_ft4_ru_norm'
SEM_MODEL_PATH = DATA_PATH + f'models/{SEM_MODEL_NAME}/'
EVENTS_PATH = DATA_PATH + 'events/cleaned/events.csv'
TMP_PATH = f'{DATA_PATH}tmp/{SEM_MODEL_NAME}_new/'

'success'

#samples = list(range(30, 101, 10)) + [75, 125, 128] 
#n_semantic = list(range(40, 130, 10)) + [150, 250, 500, 750, 1000]
n_semantic = list(range(10, 151, 10)) + list(range(200, 1001, 100))
n_clusters = list(range(5, 151))

In [ ]:
import semlib
!mkdir {TMP_PATH}

for n in n_semantic:
    df, X = semlib.prepare_model(TMP_PATH, EVENTS_PATH, SEM_MODEL_PATH, n)
    path = f'{TMP_PATH}{n}/'
    # saving results of this cell
    np.save(path + 'X.npy', X)
    df.to_csv(r'' + path + 'df.csv', index=False)
    print(f'completed for {n}')

print('completed')

In [ ]:
for n in n_semantic:
    suffix = f'{n}/'
    path = TMP_PATH + suffix
    df = pd.read_csv(path + 'df.csv')
    X = np.load(path + 'X.npy')
    
    df, df_scores = semlib.k_means_list(n_clusters, df, X)
    
    df_scores.to_csv(r'' + path + 'scores.csv', index=False)
    df.to_csv(r'' + path + 'df.csv', index=False)
    print(f'completed for {n}')
    

completed for 10
completed for 20
completed for 30
completed for 40
completed for 50
completed for 60
completed for 70
completed for 80
completed for 90
completed for 100
completed for 110
completed for 120
completed for 150
completed for 250
completed for 500
completed for 750


In [ ]:
df_cross = pd.read_csv('cross_valid_union.csv')
best = (0, 0, 0)

for n in n_semantic:
    suffix = f'{n}/'
    path = TMP_PATH + suffix
    df = pd.read_csv(path + 'df.csv')
    df_scores = pd.read_csv(path + 'scores.csv')
    
    df_scores = semlib.calc_scores_list(n_clusters, df, df_cross, df_scores)
    
    best_score = df_scores.iloc[df_scores['f1'].idxmax()]
    best = (best_score['f1'], n, best_score['n_clusters']) if best_score['f1'] > best[0] else best
    
    df_scores.to_csv(r'' + path + 'scores_union.csv', index=False)

best

In [ ]:
df_cross = pd.read_csv('cross_valid_union.csv')

for n in n_semantic:
    suffix = f'{n}/'
    path = TMP_PATH + suffix
    df = pd.read_csv(path + 'df.csv')
    X = np.load(path + 'X.npy')
    
    df = semlib.agglomerative_list(n_clusters, df, X)
    df_scores = semlib.calc_scores_list(n_clusters, df, df_cross)
    
    df_scores.to_csv(r'' + path + 'scores_ag.csv', index=False)
    df.to_csv(r'' + path + 'df_ag.csv', index=False)
    
    print(f'completed for {n}')

In [7]:
best = semlib.find_best_score(n_semantic, TMP_PATH, 'scores_union.csv', 'f1')
best

(0.7944664031620552, 120, 62)

In [8]:
best = semlib.find_best_score(n_semantic, TMP_PATH, 'scores_ag.csv', 'f1')
best

(0.7901234567901235, 120, 29)

In [9]:
fig = semlib.score_plot_3d(n_semantic, n_clusters, TMP_PATH, 'scores_ag.csv', scores_name='f1')
fig.show()

In [10]:
fig = semlib.score_plot_3d(n_semantic, n_clusters, TMP_PATH, 'scores_union.csv', scores_name='f1')
fig.show()

In [11]:
best = semlib.find_best_score(n_semantic, TMP_PATH, 'scores_ag.csv', 'f1')
print(f'score: {best[0]}, optimal_n_semantic: {best[1]}, optimal_n_clusters: {best[2]}')
model = f'{best[1]}/'
df = tools.read_events(TMP_PATH + model + 'df_ag.csv')
df_scores = pd.read_csv(TMP_PATH + model + 'scores_ag.csv')

tools.plot_score(df_scores, y=['f1', 'recall', 'precision']).show()

tools.plot_clusters(df, str(best[2])).show()

df_centroids = tools.create_centroids(df, int(best[2]), use_norm=False, hashtags_size=20)
fig, df_filtered = tools.plot_centroids(df_centroids, size_max=80, size_text_tags=1)
fig.show()
len(df_filtered)

score: 0.7901234567901235, optimal_n_semantic: 120, optimal_n_clusters: 29


29

In [57]:
from importlib import reload
reload(semlib)
reload(tools)
from tools import find_best, plot_score, plot_clusters

In [ ]:
df_cross = pd.read_csv('cross_valid_union.csv')

for n in [40]:
    suffix = f'{n}/'
    path = TMP_PATH + suffix
    df = pd.read_csv(path + 'df.csv')
    X = np.load(path + 'X.npy')
    
    df = semlib.agglomerative_list(n_clusters, df, X)
    df_scores = semlib.calc_scores_list(n_clusters, df, df_cross)
    
    #df_scores.to_csv(r'' + path + 'scores_ag.csv', index=False)
    #df.to_csv(r'' + path + 'df_ag.csv', index=False)
    
    print(f'completed for {n}')

In [30]:
best

(0.8127413127413128, 40, 25.0)

In [25]:
import tools
from tools import find_best, plot_score, plot_clusters

model = '40/'
opt_clusters = 25

df = tools.read_events(TMP_PATH + model + 'df_ag.csv')
df_scores = pd.read_csv(TMP_PATH + model + 'scores_ag.csv')

print('f1:', find_best(df_scores, 'f1'))

_ = plot_score(df_scores, y=['f1', 'recall', 'precision'])

plot_clusters(df, str(opt_clusters))

df_centroids = tools.create_centroids(df, opt_clusters, use_norm=False, hashtags_size=20)
tools.plot_centroids(df_centroids, 100)

df_centroids2 = df_centroids[df_centroids['len'] > 5]
df_centroids2['text'] = df_centroids['hover_name'].apply(lambda s: '<br>'.join(s.split('<br>')[:2]))
fig = px.scatter(df_centroids2, x="x", y="y", color='label', text='text', size='len', hover_name='hover_name', size_max=80)
fig.show()
len(df_centroids2['label'].unique())

f1: (0.8127413127413128, 25.0)


25

In [16]:
best = semlib.find_best_score(n_semantic, DATA_PATH + 'tmp/sm_wv3_ru_norm_new/', 'scores_union.csv', 'f1')
print(f'score: {best[0]}, optimal_n_semantic: {best[1]}, optimal_n_clusters: {best[2]}')
model = f'{best[1]}/'
df = tools.read_events(TMP_PATH + model + 'df_ag.csv')
df_scores = pd.read_csv(TMP_PATH + model + 'scores_ag.csv')

tools.plot_score(df_scores, y=['f1', 'recall', 'precision']).show()

tools.plot_clusters(df, str(best[2])).show()

df_centroids = tools.create_centroids(df, int(best[2]), use_norm=False, hashtags_size=20)
fig, df_filtered = tools.plot_centroids(df_centroids, size_max=80, size_text_tags=1)
fig.show()
len(df_filtered)

score: 0.8621873467385974, optimal_n_semantic: 70, optimal_n_clusters: 52


52